In [2]:
import sys
import numpy as np
import pandas as pd
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix
from sklearn.model_selection import GridSearchCV, cross_val_score
if __name__ == '__main__':

    filename = 'creditcard_2023.csv'
    # Load csv data
    df = pd.read_csv(filename)

    # Split data into X/y and training/testing
    X = df.drop(['id', 'Class'], axis=1)
    y = df['Class']
    X_train, X_test, y_train, y_test = train_test_split(X, y,
                                                        test_size=0.20,
                                                        random_state=1337)
    #basic tree
    tree = DecisionTreeClassifier(random_state=1337)
    tree.fit(X_train, y_train)

    tree_params = {'max_depth': range(1,10),
               'max_features': range(4,25)}
    tree_cv = GridSearchCV(tree, tree_params, cv=5, n_jobs=-1, verbose=True)
    tree_cv.fit(X_train, y_train)



   #predictions
    predictions = tree.predict(X_test)
    predictions_cv = tree_cv.predict(X_test)


    # Display metrics
    print('Accuracy score: {}'.format(accuracy_score(y_test, predictions)))
    print('Precision score: {}'.format(precision_score(y_test, predictions)))
    print('Recall score: {}'.format(recall_score(y_test, predictions)))
    print('F1 score: {}'.format(f1_score(y_test, predictions)))
    cm = confusion_matrix(y_test, predictions)
    tn, fp, fn, tp = cm.ravel()
    print('Confusion matrix (Basic Decision Tree):')
    print(cm)

    # Calculate and print FPR, FNR, TPR
    fpr = fp / (fp + tn)
    fnr = fn / (fn + tp)
    tpr = tp / (tp + fn)
    print(f"Basic Decision Tree - FPR: {fpr:.4f}, FNR: {fnr:.4f}, TPR: {tpr:.4f}")

   # Confusion matrix for GridSearchCV optimized tree
    cm_cv = confusion_matrix(y_test, predictions_cv)
    tn_cv, fp_cv, fn_cv, tp_cv = cm_cv.ravel()
    print('Confusion matrix (GridSearchCV Decision Tree):')
    print(cm_cv)

    # Calculate and print FPR, FNR, TPR for GridSearchCV optimized tree
    fpr_cv = fp_cv / (fp_cv + tn_cv)
    fnr_cv = fn_cv / (fn_cv + tp_cv)
    tpr_cv = tp_cv / (tp_cv + fn_cv)
    print(f"GridSearchCV Decision Tree - FPR: {fpr_cv:.4f}, FNR: {fnr_cv:.4f}, TPR: {tpr_cv:.4f}")

    # Display results of GridSearchCV
    print(f"Best parameters are {tree_cv.best_params_}")
    print('GridSearchCV best score: {:.4f}'.format(tree_cv.best_score_))
    print('Accuracy score (GridSearchCV): {}'.format(accuracy_score(y_test, predictions_cv)))
    print('Precision score (GridSearchCV): {}'.format(precision_score(y_test, predictions_cv)))
    print('Recall score (GridSearchCV): {}'.format(recall_score(y_test, predictions_cv)))
    print('F1 score (GridSearchCV): {}'.format(f1_score(y_test, predictions_cv)))

Fitting 5 folds for each of 189 candidates, totalling 945 fits
Accuracy score: 0.9980215605930043
Precision score: 0.9973069543942408
Recall score: 0.9987308749911866
F1 score: 0.9980184067990665
Confusion matrix (Basic Decision Tree):
[[56841   153]
 [   72 56660]]
Basic Decision Tree - FPR: 0.0027, FNR: 0.0013, TPR: 0.9987
Confusion matrix (GridSearchCV Decision Tree):
[[55709  1285]
 [ 1478 55254]]
GridSearchCV Decision Tree - FPR: 0.0225, FNR: 0.0261, TPR: 0.9739
Best parameters are {'max_depth': 9, 'max_features': 23}
GridSearchCV best score: 0.9818
Accuracy score (GridSearchCV): 0.9757047640820921
Precision score (GridSearchCV): 0.9772723252975822
Recall score (GridSearchCV): 0.9739476838468589
F1 score (GridSearchCV): 0.9756071721799932


In [ ]:
from sklearn.tree import DecisionTreeClassifier
import pydotplus
from sklearn.tree import export_graphviz

# Let’s write an auxiliary function that will return grid for further visualization.

def tree_graph_to_png(tree, feature_names, png_file_to_save):
    tree_str = export_graphviz(tree, feature_names=feature_names,
                                     filled=True, out_file=None)
    graph = pydotplus.graph_from_dot_data(tree_str)
    graph.write_png(png_file_to_save)


def get_grid(data):
    x_min, x_max = data[:, 0].min() - 1, data[:, 0].max() + 1
    y_min, y_max = data[:, 1].min() - 1, data[:, 1].max() + 1
    return np.meshgrid(np.arange(x_min, x_max, 0.01), np.arange(y_min, y_max, 0.01))

feature_names = df.drop(['id', 'Class'], axis=1).columns

tree_graph_to_png(tree=tree, feature_names=feature_names, png_file_to_save='tree.png')

from IPython.display import Image
from IPython.core.display import HTML
PATH = "tree.png"
Image(filename = PATH , width=900, height=900)

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.665131 to fit



For emsemeble method

In [ ]:
import sys
import numpy as np
import pandas as pd
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.model_selection import GridSearchCV

if __name__ == '__main__':
    # Load training and testing data
    train_filename = 'DM_creditcard_2023_train_90_percent.csv'
    test_filename = 'DM_creditcard_2023_test_10_percent.csv'

    train_df = pd.read_csv(train_filename)
    test_df = pd.read_csv(test_filename)

    # Split data into X/y for both training and testing
    X_train = train_df.drop(['id', 'Class_label'], axis=1)
    y_train = train_df['Class_label']
    X_test = test_df.drop(['id' ,'Class_label'], axis=1)
    y_test = test_df['Class_label']

    # Basic Decision Tree
    tree = DecisionTreeClassifier(random_state=1337)
    tree.fit(X_train, y_train)


    # Predictions
    predictions = tree.predict(X_test)


    # Display metrics
    print('Accuracy score:', accuracy_score(y_test, predictions))
    print('Precision score:', precision_score(y_test, predictions))
    print('Recall score:', recall_score(y_test, predictions))
    print('F1 score:', f1_score(y_test, predictions))

    # Save predictions
    test_df['Predicted_Class'] = predictions
    test_df.to_csv('Predictions.csv', index=False)

Accuracy score: 0.998100698169284
Precision score: 0.9972896867300246
Recall score: 0.9989070652940347
F1 score: 0.9980977207876846
